## Checking Versions

In [2]:
# Check nvcc version
!nvcc -V

# Check GCC version
!gcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2020 NVIDIA Corporation
Built on Mon_Oct_12_20:09:46_PDT_2020
Cuda compilation tools, release 11.1, V11.1.105
Build cuda_11.1.TC455_06.29190527_0
gcc (Ubuntu 7.5.0-3ubuntu1~18.04) 7.5.0
Copyright (C) 2017 Free Software Foundation, Inc.
This is free software; see the source for copying conditions.  There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.



# Installing and Importing Libraries

In [3]:
# install dependencies: (use cu111 because colab has CUDA 11.1)
!pip install torch==1.9.0+cu111 torchvision==0.10.0+cu111 -f https://download.pytorch.org/whl/torch_stable.html

# install mmcv-full thus we could use CUDA operators
!pip install mmcv-full -f https://download.openmmlab.com/mmcv/dist/cu111/torch1.9.0/index.html

# Install mmaction2
!rm -rf mmaction2
!git clone https://github.com/open-mmlab/mmaction2.git
%cd mmaction2

!pip install -e .

# Install some optional requirements
!pip install -r requirements/optional.txt

Looking in links: https://download.pytorch.org/whl/torch_stable.html
     |█████████████                   | 834.1 MB 1.5 MB/s eta 0:13:46tcmalloc: large alloc 1147494400 bytes == 0x39be4000 @  0x7f88f16ac615 0x592b76 0x4df71e 0x59afff 0x515655 0x549576 0x593fce 0x548ae9 0x51566f 0x549576 0x593fce 0x548ae9 0x5127f1 0x598e3b 0x511f68 0x598e3b 0x511f68 0x598e3b 0x511f68 0x4bc98a 0x532e76 0x594b72 0x515600 0x549576 0x593fce 0x548ae9 0x5127f1 0x549576 0x593fce 0x5118f8 0x593dd7
     |████████████████▌               | 1055.7 MB 1.3 MB/s eta 0:12:22tcmalloc: large alloc 1434370048 bytes == 0x7e23a000 @  0x7f88f16ac615 0x592b76 0x4df71e 0x59afff 0x515655 0x549576 0x593fce 0x548ae9 0x51566f 0x549576 0x593fce 0x548ae9 0x5127f1 0x598e3b 0x511f68 0x598e3b 0x511f68 0x598e3b 0x511f68 0x4bc98a 0x532e76 0x594b72 0x515600 0x549576 0x593fce 0x548ae9 0x5127f1 0x549576 0x593fce 0x5118f8 0x593dd7
     |█████████████████████           | 1336.2 MB 1.2 MB/s eta 0:09:27tcmalloc: large alloc 1792966656 bytes =

In [4]:
# Check Pytorch installation
import torch, torchvision
print(torch.__version__, torch.cuda.is_available())

# Check MMAction2 installation
import mmaction
print(mmaction.__version__)

# Check MMCV installation
from mmcv.ops import get_compiling_cuda_version, get_compiler_version

print(get_compiling_cuda_version())
print(get_compiler_version())

1.9.0+cu111 True
0.24.0
11.1
GCC 7.3


# Setting Up MLOPS to Track Experiment

In [5]:
! pip install mlflow

     |████████████████████████████████| 17.8 MB 5.2 MB/s 
     |████████████████████████████████| 62 kB 980 kB/s 
     |████████████████████████████████| 210 kB 55.6 MB/s 
     |████████████████████████████████| 596 kB 59.8 MB/s 
     |████████████████████████████████| 146 kB 17.4 MB/s 
     |████████████████████████████████| 181 kB 57.1 MB/s 
     |████████████████████████████████| 79 kB 7.0 MB/s 
     |████████████████████████████████| 54 kB 3.4 MB/s 
     |████████████████████████████████| 63 kB 1.9 MB/s 
     |████████████████████████████████| 78 kB 4.4 MB/s 
  Created wheel for databricks-cli: filename=databricks_cli-0.16.6-py3-none-any.whl size=112631 sha256=5f712b89593b10923d204cc976fa591603636639a880d1d8d4d85829b5298dfd
  Stored in directory: /root/.cache/pip/wheels/96/c1/f8/d75a22e789ab6a4dff11f18338c3af4360189aa371295cc934
Successfully built databricks-cli
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfu

In [6]:
!databricks configure --host https://community.cloud.databricks.com/

Username: aryan.jadon@sjsu.edu
Password: 
Repeat for confirmation: 


In [7]:
import mlflow

mlflow.set_tracking_uri("databricks")
mlflow.set_experiment("/Users/aryan.jadon@sjsu.edu/Deep-Learning-Project")

<Experiment: artifact_location='dbfs:/databricks/mlflow-tracking/566514200710364', experiment_id='566514200710364', lifecycle_stage='active', name='/Users/aryan.jadon@sjsu.edu/Deep-Learning-Project', tags={'mlflow.experiment.sourceName': '/Users/aryan.jadon@sjsu.edu/Deep-Learning-Project',
 'mlflow.experimentType': 'MLFLOW_EXPERIMENT',
 'mlflow.ownerEmail': 'aryan.jadon@sjsu.edu',
 'mlflow.ownerId': '3793239263173249'}>

In [8]:
# running experiment
current_run = mlflow.start_run()
mlflow.sklearn.autolog()

# Settings up Checkpoints and Configs

In [9]:
!mkdir checkpoints
!wget -c https://download.openmmlab.com/mmaction/recognition/tsn/tsn_r50_1x1x3_100e_kinetics400_rgb/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth \
      -O checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth

--2022-05-22 07:27:14--  https://download.openmmlab.com/mmaction/recognition/tsn/tsn_r50_1x1x3_100e_kinetics400_rgb/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth
Resolving download.openmmlab.com (download.openmmlab.com)... 47.252.96.28
Connecting to download.openmmlab.com (download.openmmlab.com)|47.252.96.28|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 97579339 (93M) [application/octet-stream]
Saving to: ‘checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth’

checkpoints/tsn_r50 100%[===================>]  93.06M  8.67MB/s    in 12s     

2022-05-22 07:27:27 (8.01 MB/s) - ‘checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth’ saved [97579339/97579339]



In [10]:
from mmaction.apis import inference_recognizer, init_recognizer

# Choose to use a config and initialize the recognizer
config = 'configs/recognition/tsn/tsn_r50_video_inference_1x1x3_100e_kinetics400_rgb.py'

# Setup a checkpoint file to load
checkpoint = 'checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth'

# Initialize the recognizer
model = init_recognizer(config, checkpoint, device='cuda:0')

load checkpoint from local path: checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth


# Model Training

## Downloading Dataset 

#### Firstly, let's download a tiny dataset obtained from [Kinetics-400](https://deepmind.com/research/open-source/open-source-datasets/kinetics/). 

#### We select 30 videos with their labels as train dataset and 10 videos with their labels as test dataset.

In [11]:
# download, decompress the data
!rm kinetics400_tiny.zip*
!rm -rf kinetics400_tiny
!wget https://download.openmmlab.com/mmaction/kinetics400_tiny.zip
!unzip kinetics400_tiny.zip > /dev/null

rm: cannot remove 'kinetics400_tiny.zip*': No such file or directory
--2022-05-22 07:27:34--  https://download.openmmlab.com/mmaction/kinetics400_tiny.zip
Resolving download.openmmlab.com (download.openmmlab.com)... 47.252.96.28
Connecting to download.openmmlab.com (download.openmmlab.com)|47.252.96.28|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 18308682 (17M) [application/zip]
Saving to: ‘kinetics400_tiny.zip’

kinetics400_tiny.zi 100%[===================>]  17.46M  6.38MB/s    in 2.7s    

2022-05-22 07:27:37 (6.38 MB/s) - ‘kinetics400_tiny.zip’ saved [18308682/18308682]



In [12]:
# Check the directory structure of the tiny data
# Install tree first

! apt-get -q install tree
! tree kinetics400_tiny

Reading package lists...
Building dependency tree...
Reading state information...
The following package was automatically installed and is no longer required:
  libnvidia-common-460
Use 'apt autoremove' to remove it.
The following NEW packages will be installed:
  tree
0 upgraded, 1 newly installed, 0 to remove and 42 not upgraded.
Need to get 40.7 kB of archives.
After this operation, 105 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu bionic/universe amd64 tree amd64 1.7.0-5 [40.7 kB]
Fetched 40.7 kB in 0s (180 kB/s)
Selecting previously unselected package tree.
(Reading database ... 155629 files and directories currently installed.)
Preparing to unpack .../tree_1.7.0-5_amd64.deb ...
Unpacking tree (1.7.0-5) ...
Setting up tree (1.7.0-5) ...
Processing triggers for man-db (2.8.3-2ubuntu0.1) ...
kinetics400_tiny
├── kinetics_tiny_train_video.txt
├── kinetics_tiny_val_video.txt
├── train
│   ├── 27_CSXByd3s.mp4
│   ├── 34XczvTaRiI.mp4
│   ├── A-wiliK50Z

According to the format defined in [`VideoDataset`](./datasets/video_dataset.py), each line indicates a sample video with the filepath and label, which are split with a whitespace.

In [13]:
# After downloading the data, we need to check the annotation format
! cat kinetics400_tiny/kinetics_tiny_train_video.txt

D32_1gwq35E.mp4 0
iRuyZSKhHRg.mp4 1
oXy-e_P_cAI.mp4 0
34XczvTaRiI.mp4 1
h2YqqUhnR34.mp4 0
O46YA8tI530.mp4 0
kFC3KY2bOP8.mp4 1
WWP5HZJsg-o.mp4 1
phDqGd0NKoo.mp4 1
yLC9CtWU5ws.mp4 0
27_CSXByd3s.mp4 1
IyfILH9lBRo.mp4 1
T_TMNGzVrDk.mp4 1
TkkZPZHbAKA.mp4 0
PnOe3GZRVX8.mp4 1
soEcZZsBmDs.mp4 1
FMlSTTpN3VY.mp4 1
WaS0qwP46Us.mp4 0
A-wiliK50Zw.mp4 1
oMrZaozOvdQ.mp4 1
ZQV4U2KQ370.mp4 0
DbX8mPslRXg.mp4 1
h10B9SVE-nk.mp4 1
P5M-hAts7MQ.mp4 0
R8HXQkdgKWA.mp4 0
D92m0HsHjcQ.mp4 0
RqnKtCEoEcA.mp4 0
LvcFDgCAXQs.mp4 0
xGY2dP0YUjA.mp4 0
Wh_YPQdH1Zg.mp4 0


### Modify the config

In the next step, we need to modify the config for the training.
To accelerate the process, we finetune a recognizer using a pre-trained recognizer.

In [14]:
from mmcv import Config
cfg = Config.fromfile('./configs/recognition/tsn/tsn_r50_video_1x1x8_100e_kinetics400_rgb.py')

In [15]:
for key,value in cfg.items():
  try:
    mlflow.log_param(key,value)
  except Exception as e:
    pass

Given a config that trains a TSN model on kinetics400-full dataset, we need to modify some values to use it for training TSN on Kinetics400-tiny dataset.


In [16]:
from mmcv.runner import set_random_seed

# Modify dataset type and path
cfg.dataset_type = 'VideoDataset'
cfg.data_root = 'kinetics400_tiny/train/'
cfg.data_root_val = 'kinetics400_tiny/val/'
cfg.ann_file_train = 'kinetics400_tiny/kinetics_tiny_train_video.txt'
cfg.ann_file_val = 'kinetics400_tiny/kinetics_tiny_val_video.txt'
cfg.ann_file_test = 'kinetics400_tiny/kinetics_tiny_val_video.txt'

cfg.data.test.type = 'VideoDataset'
cfg.data.test.ann_file = 'kinetics400_tiny/kinetics_tiny_val_video.txt'
cfg.data.test.data_prefix = 'kinetics400_tiny/val/'

cfg.data.train.type = 'VideoDataset'
cfg.data.train.ann_file = 'kinetics400_tiny/kinetics_tiny_train_video.txt'
cfg.data.train.data_prefix = 'kinetics400_tiny/train/'

cfg.data.val.type = 'VideoDataset'
cfg.data.val.ann_file = 'kinetics400_tiny/kinetics_tiny_val_video.txt'
cfg.data.val.data_prefix = 'kinetics400_tiny/val/'

# The flag is used to determine whether it is omnisource training
cfg.setdefault('omnisource', False)
# Modify num classes of the model in cls_head
cfg.model.cls_head.num_classes = 2
# We can use the pre-trained TSN model
cfg.load_from = './checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth'

# Set up working dir to save files and logs.
cfg.work_dir = './tutorial_exps'

# The original learning rate (LR) is set for 8-GPU training.
# We divide it by 8 since we only use one GPU.
cfg.data.videos_per_gpu = cfg.data.videos_per_gpu // 16
cfg.optimizer.lr = cfg.optimizer.lr / 8 / 16
cfg.total_epochs = 10

# We can set the checkpoint saving interval to reduce the storage cost
cfg.checkpoint_config.interval = 5
# We can set the log print interval to reduce the the times of printing log
cfg.log_config.interval = 5

# Set seed thus the results are more reproducible
cfg.seed = 0
set_random_seed(0, deterministic=False)
cfg.gpu_ids = range(1)

# Save the best
cfg.evaluation.save_best='auto'


# We can initialize the logger for training and have a look
# at the final config used for training
print(f'Config:\n{cfg.pretty_text}')


Config:
model = dict(
    type='Recognizer2D',
    backbone=dict(
        type='ResNet',
        pretrained='torchvision://resnet50',
        depth=50,
        norm_eval=False),
    cls_head=dict(
        type='TSNHead',
        num_classes=2,
        in_channels=2048,
        spatial_type='avg',
        consensus=dict(type='AvgConsensus', dim=1),
        dropout_ratio=0.4,
        init_std=0.01),
    train_cfg=None,
    test_cfg=dict(average_clips=None))
optimizer = dict(type='SGD', lr=7.8125e-05, momentum=0.9, weight_decay=0.0001)
optimizer_config = dict(grad_clip=dict(max_norm=40, norm_type=2))
lr_config = dict(policy='step', step=[40, 80])
total_epochs = 10
checkpoint_config = dict(interval=5)
log_config = dict(interval=5, hooks=[dict(type='TextLoggerHook')])
dist_params = dict(backend='nccl')
log_level = 'INFO'
load_from = './checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth'
resume_from = None
workflow = [('train', 1)]
opencv_num_threads = 0
mp_start_method = '

In [17]:
# mlflow
for key,value in cfg.items():
  try:
    mlflow.log_param(key,value)
  except Exception as e:
    pass

### Training Recognizer

In [18]:
import os.path as osp
from mmaction.datasets import build_dataset
from mmaction.models import build_model
from mmaction.apis import train_model
import mmcv

# Build the dataset
datasets = [build_dataset(cfg.data.train)]

# Build the recognizer
model = build_model(cfg.model, train_cfg=cfg.get('train_cfg'), test_cfg=cfg.get('test_cfg'))

load checkpoint from torchvision path: torchvision://resnet50


Downloading: "https://download.pytorch.org/models/resnet50-0676ba61.pth" to /root/.cache/torch/hub/checkpoints/resnet50-0676ba61.pth


  0%|          | 0.00/97.8M [00:00<?, ?B/s]

2022-05-22 07:27:52,316 - mmaction - INFO - These parameters in pretrained checkpoint are not loaded: {'fc.bias', 'fc.weight'}


In [19]:
# Create work_dir
mmcv.mkdir_or_exist(osp.abspath(cfg.work_dir))
train_model(model, datasets, cfg, distributed=False, validate=True)

2022-05-22 07:27:52,383 - mmaction - INFO - load checkpoint from local path: ./checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth
2022-05-22 07:27:52,471 - mmaction - WARNING - The model and loaded state dict do not match exactly

size mismatch for cls_head.fc_cls.weight: copying a param with shape torch.Size([400, 2048]) from checkpoint, the shape in current model is torch.Size([2, 2048]).
size mismatch for cls_head.fc_cls.bias: copying a param with shape torch.Size([400]) from checkpoint, the shape in current model is torch.Size([2]).
2022-05-22 07:27:52,474 - mmaction - INFO - Start running, host: root@0835d9698af7, work_dir: /content/mmaction2/tutorial_exps
2022-05-22 07:27:52,476 - mmaction - INFO - Hooks will be executed in the following order:
before_run:
(VERY_HIGH   ) StepLrUpdaterHook                  
(NORMAL      ) CheckpointHook                     
(LOW         ) EvalHook                           
(VERY_LOW    ) TextLoggerHook                     
 ----

[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 10/10, 5.4 task/s, elapsed: 2s, ETA:     0s

2022-05-22 07:28:28,997 - mmaction - INFO - Evaluating top_k_accuracy ...
2022-05-22 07:28:28,999 - mmaction - INFO - 
top1_acc	0.7000
top5_acc	1.0000
2022-05-22 07:28:29,002 - mmaction - INFO - Evaluating mean_class_accuracy ...
2022-05-22 07:28:29,006 - mmaction - INFO - 
mean_acc	0.7000
2022-05-22 07:28:29,861 - mmaction - INFO - Now best checkpoint is saved as best_top1_acc_epoch_5.pth.
2022-05-22 07:28:29,863 - mmaction - INFO - Best top1_acc is 0.7000 at 5 epoch.
2022-05-22 07:28:29,867 - mmaction - INFO - Epoch(val) [5][5]	top1_acc: 0.7000, top5_acc: 1.0000, mean_class_accuracy: 0.7000
2022-05-22 07:28:33,722 - mmaction - INFO - Epoch [6][5/15]	lr: 7.813e-05, eta: 0:00:32, time: 0.769, data_time: 0.560, memory: 1656, top1_acc: 0.7000, top5_acc: 1.0000, loss_cls: 0.6413, loss: 0.6413, grad_norm: 12.5310
2022-05-22 07:28:35,044 - mmaction - INFO - Epoch [6][10/15]	lr: 7.813e-05, eta: 0:00:29, time: 0.265, data_time: 0.075, memory: 1656, top1_acc: 0.5000, top5_acc: 1.0000, loss_cls

[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 10/10, 5.5 task/s, elapsed: 2s, ETA:     0s

2022-05-22 07:29:05,290 - mmaction - INFO - Evaluating top_k_accuracy ...
2022-05-22 07:29:05,291 - mmaction - INFO - 
top1_acc	0.8000
top5_acc	1.0000
2022-05-22 07:29:05,296 - mmaction - INFO - Evaluating mean_class_accuracy ...
2022-05-22 07:29:05,300 - mmaction - INFO - 
mean_acc	0.8000
2022-05-22 07:29:05,336 - mmaction - INFO - The previous best checkpoint /content/mmaction2/tutorial_exps/best_top1_acc_epoch_5.pth was removed
2022-05-22 07:29:06,162 - mmaction - INFO - Now best checkpoint is saved as best_top1_acc_epoch_10.pth.
2022-05-22 07:29:06,165 - mmaction - INFO - Best top1_acc is 0.8000 at 10 epoch.
2022-05-22 07:29:06,167 - mmaction - INFO - Epoch(val) [10][5]	top1_acc: 0.8000, top5_acc: 1.0000, mean_class_accuracy: 0.8000


### Understanding the log

From the log, we can have a basic understanding the training process and know how well the recognizer is trained.

Firstly, the ResNet-50 backbone pre-trained on ImageNet is loaded, this is a common practice since training from scratch is more cost. The log shows that all the weights of the ResNet-50 backbone are loaded except the `fc.bias` and `fc.weight`.

Second, since the dataset we are using is small, we loaded a TSN model and finetune it for action recognition.
The original TSN is trained on original Kinetics-400 dataset which contains 400 classes but Kinetics-400 Tiny dataset only have 2 classes. Therefore, the last FC layer of the pre-trained TSN for classification has different weight shape and is not used.

Third, after training, the recognizer is evaluated by the default evaluation. The results show that the recognizer achieves 100% top1 accuracy and 100% top5 accuracy on the val dataset.

### Testing the trained recognizer

After finetuning the recognizer, let's check the prediction results!

In [20]:
from mmaction.apis import single_gpu_test
from mmaction.datasets import build_dataloader
from mmcv.parallel import MMDataParallel

# Build a test dataloader
dataset = build_dataset(cfg.data.test, dict(test_mode=True))
data_loader = build_dataloader(
        dataset,
        videos_per_gpu=1,
        workers_per_gpu=cfg.data.workers_per_gpu,
        dist=False,
        shuffle=False)

model = MMDataParallel(model, device_ids=[0])
outputs = single_gpu_test(model, data_loader)

eval_config = cfg.evaluation
eval_config.pop('interval')

eval_res = dataset.evaluate(outputs, **eval_config)

for name, val in eval_res.items():
    print(f'{name}: {val:.04f}')
    mlflow.log_param(name,val)

[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 10/10, 0.6 task/s, elapsed: 16s, ETA:     0s
Evaluating top_k_accuracy ...

top1_acc	0.8000
top5_acc	1.0000

Evaluating mean_class_accuracy ...

mean_acc	0.8000
top1_acc: 0.8000


/content/mmaction2/mmaction/datasets/base.py:167: UserWarning: Option arguments for metrics has been changed to `metric_options`, See 'https://github.com/open-mmlab/mmaction2/pull/286' for more details
  'Option arguments for metrics has been changed to '


top5_acc: 1.0000
mean_class_accuracy: 0.8000


In [30]:
torch.save(model, "/content/model_weights.t7")

# Perform Spatio-Temporal Detection

In [21]:
# Git clone mmdetection repo
%cd ..
!git clone https://github.com/open-mmlab/mmdetection.git
%cd mmdetection

# install mmdet
!pip install -e .
%cd ../mmaction2

/content
Cloning into 'mmdetection'...
remote: Enumerating objects: 24695, done.
remote: Counting objects: 100% (48/48), done.
remote: Compressing objects: 100% (43/43), done.
remote: Total 24695 (delta 9), reused 32 (delta 5), pack-reused 24647
Receiving objects: 100% (24695/24695), 37.65 MiB | 32.89 MiB/s, done.
Resolving deltas: 100% (17313/17313), done.
/content/mmdetection
Obtaining file:///content/mmdetection
  Running setup.py develop for mmdet
/content/mmaction2


## Downloading Video

In [22]:
!wget "https://raw.githubusercontent.com/deep-learners-sjsu/CMPE-258-Sec-49-Deep-Learning-Project/main/videos/test_video.mp4"

--2022-05-22 07:29:40--  https://raw.githubusercontent.com/deep-learners-sjsu/CMPE-258-Sec-49-Deep-Learning-Project/main/videos/test_video.mp4
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4864186 (4.6M) [application/octet-stream]
Saving to: ‘test_video.mp4’

test_video.mp4      100%[===================>]   4.64M  --.-KB/s    in 0.07s   

2022-05-22 07:29:40 (64.5 MB/s) - ‘test_video.mp4’ saved [4864186/4864186]



## Run spatio-temporal

In [23]:
!python demo/demo_spatiotemporal_det.py --video test_video.mp4

Imageio: 'ffmpeg-linux64-v3.3.1' was not found on your computer; downloading it now.
Try 1. Download from https://github.com/imageio/imageio-binaries/raw/master/ffmpeg/ffmpeg-linux64-v3.3.1 (43.8 MB)
Downloading: 8192/45929032 bytes (0.0%)1884160/45929032 bytes (4.1%)4341760/45929032 bytes (9.5%)7233536/45929032 bytes (15.7%)9773056/45929032 bytes (21.3%)12492800/45929032 bytes (27.2%)15122432/45929032 bytes (32.9%)17440768/45929032 bytes (38.0%)20316160/45929032 bytes (44.2%)22781952/45929032 bytes (49.6%)25485312/45929032 bytes (55.5%)28000256/45929032 bytes (61.0%)30531584/45929032 bytes (66.5%)328

In [24]:
# Check the video

from IPython.display import HTML
from base64 import b64encode

mp4 = open('demo/stdet_demo.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=800 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

In [25]:
mlflow.end_run()